In [43]:
import torch 
import torch.nn.functional as F
from torch.distributions import Categorical
import torch.nn as nn
import numpy as np
import random
random.seed(1999)



class simple_net(nn.Module):
    def __init__(self):
        super(simple_net, self).__init__()
        self.linear1 = nn.Linear(1, 20)
        self.linear2 = nn.Linear(20, 3)
        

    def forward(self, x):
#         print("Q_Net: Input " + "-" *5)
#         print(x.shape)
#         print(x)
#         print("Q_Net: Input " + "-" *5)
        x = x.view(-1,1)
        x = F.tanh(self.linear1(x))
        #x = F.softmax(self.linear2(x), dim=0)
        x = F.tanh(self.linear2(x))
        x = x.view(-1,3)
        #print(x.shape)
        #print(x)
        return x
    
    
from collections import namedtuple
Transition = namedtuple('Transition',
                        ('state', 'action', 'y_hat'))


class ReplayMemory(object):

    def __init__(self, capacity):
        self.capacity = capacity
        self.memory = []
        self.position = 0

    def push(self, *args):
        """Saves a transition."""
        if len(self.memory) < self.capacity:
            self.memory.append(None)
        self.memory[self.position] = Transition(*args)
        self.position = (self.position + 1) % self.capacity

    def sample(self, batch_size):
        return random.sample(self.memory, batch_size)

    def __len__(self):
        return len(self.memory)
    
# custom weights initialization 
def weights_init(m):
    classname = m.__class__.__name__
    #print classname
    #print q_net
    if classname.find('Linear') != -1:
        m.weight.data.normal_(0.01, 0.03)
        #if not m.bias is None:
        #    m.bias.data.normal_(0.1, 0.02)
        #m.weight.data.uniform_(0.0, 0.02)        
        #m.weight.data.fill_(0.01)
        if not m.bias is None:
            m.bias.data.fill_(0.0)
        print m
        
        
log_sf = nn.LogSoftmax(dim=1)
use_cuda = torch.cuda.is_available()
FloatTensor = torch.cuda.FloatTensor if use_cuda else torch.FloatTensor
LongTensor = torch.cuda.LongTensor if use_cuda else torch.LongTensor
ByteTensor = torch.cuda.ByteTensor if use_cuda else torch.ByteTensor
Tensor = FloatTensor
BATCH_SIZE = 100
MEMORY_SIZE = 500
memory = ReplayMemory(MEMORY_SIZE)
TRAIN_STEPS = 10000
loss_cum = []
sim_net = simple_net()
sim_net.apply(weights_init)
import torch.optim as optim
optimizer = optim.Adam(sim_net.parameters(), lr=0.001)
#Y = torch.randint(0,4, (20,))

Y = np.array([[0,1,0],
             [1,0,1],
             [0,1,0],
             [1,0,1]])
Y = torch.from_numpy(Y)

X = torch.range(0,3)

print(Y)
print(X)


Linear(in_features=1, out_features=20, bias=True)
Linear(in_features=20, out_features=3, bias=True)
tensor([[ 0,  1,  0],
        [ 1,  0,  1],
        [ 0,  1,  0],
        [ 1,  0,  1]])
tensor([ 0.,  1.,  2.,  3.])


In [44]:

def optimize():
    #p_x_y = torch.zeros((1,4))
    
    transitions = memory.sample(BATCH_SIZE)
    batch = Transition(*zip(*transitions))
    
    states_tensor = FloatTensor(batch.state).view(BATCH_SIZE,1)
    action_tensor = LongTensor(batch.action).view(BATCH_SIZE,1)
    y_hat_tensor = FloatTensor(batch.y_hat).view(BATCH_SIZE,1)
    #y_hat_tensor = torch.cat(batch.y_hat).view(BATCH_SIZE,3)
    #y_hat_tensor = y_hat_tensor.type(FloatTensor)

    
    sim_net.train()
    res = sim_net(states_tensor)

    #print y_hat_tensor.type()
    #print values.type()
    #values = res
    values = res.gather(1,action_tensor)
    loss = torch.sum(torch.mean((y_hat_tensor - values) ** 2, 1))
    
    loss_cum.append(loss)
    #print(y_pred.requires_grad)
    #print(y_pred.grad_fn)
#     print("\tBEFOR")
#     print("loss: " + str(loss))
    #print("loss: " + str(loss) + " log_softmax_values("+str(log_softmax_values)+"): ")
    #print("values: "+ str(res))
    #print("softmax: "+ str(softmax_values))
    #print("softmax: "+ str(softmax_values))
    #print("loss: " + str(loss) + " ")

    optimizer.zero_grad()
    loss.backward()
    optimizer.step()

    #print("NN params")        
    #print(list(sim_net.parameters()))

#     print("\tAFTER")
#     sim_net.eval()
#     res = sim_net(states_tensor)
#     values = res
#     softmax_values = F.softmax(values, dim=1)
#     log_softmax_values = log_sf(values)
#     loss = log_softmax_values.gather(1, action_tensor) * y_hat_tensor * -1
#     loss = torch.mean(log_softmax_values)
#     print("loss: " + str(loss) + " ")

    #print("NN params")        
    #print(sim_net.parameters())

def print_net():
    print("-" * 50)
    for i in range(4):
        st = np.array(i)
        st = np.expand_dims(st, axis=0)
        sim_net.eval()
        vals = sim_net(FloatTensor(st))
        outp = " state (" +str(i) + ") "
        n = 0
        for tensr in vals:
            for cell in tensr:
                outp = outp + " A[" + str(n) + "]:(" + str(cell.item()) + ")"
                n += 1
        print(outp)



for i in range(TRAIN_STEPS):
    for j in range(4):
         for z in range(3):


            memory.push(j, z, Y[j][z].item())
            #memory.push(j, z, Y[j])
            if len(memory) > BATCH_SIZE:
                optimize()

    
    if i % 100 == 0:
        print_net()
        
        


--------------------------------------------------
 state (0)  A[0]:(0.0) A[1]:(0.0) A[2]:(0.0)
 state (1)  A[0]:(0.00230977404863) A[1]:(-0.0013245526934) A[2]:(0.000891094561666)
 state (2)  A[0]:(0.00462008453906) A[1]:(-0.00263309362344) A[2]:(0.00177279184572)
 state (3)  A[0]:(0.00693126441911) A[1]:(-0.00391004886478) A[2]:(0.00263591133989)
--------------------------------------------------
 state (0)  A[0]:(0.177648037672) A[1]:(0.742760777473) A[2]:(0.180167987943)
 state (1)  A[0]:(0.429640352726) A[1]:(0.602751731873) A[2]:(0.428487181664)
 state (2)  A[0]:(0.622265934944) A[1]:(0.400310844183) A[2]:(0.6191188097)
 state (3)  A[0]:(0.751622259617) A[1]:(0.154363289475) A[2]:(0.747715175152)
--------------------------------------------------
 state (0)  A[0]:(0.176417455077) A[1]:(0.757803857327) A[2]:(0.159765556455)
 state (1)  A[0]:(0.437436878681) A[1]:(0.632968902588) A[2]:(0.420388609171)
 state (2)  A[0]:(0.624699115753) A[1]:(0.449036747217) A[2]:(0.610283076763)
 st

--------------------------------------------------
 state (0)  A[0]:(7.9870223999e-06) A[1]:(0.998386085033) A[2]:(-3.27825546265e-07)
 state (1)  A[0]:(0.997442781925) A[1]:(7.05122947693e-05) A[2]:(0.997417807579)
 state (2)  A[0]:(-4.90695238113e-05) A[1]:(0.99621117115) A[2]:(-3.07857990265e-05)
 state (3)  A[0]:(0.996653735638) A[1]:(0.000101774930954) A[2]:(0.996626794338)
--------------------------------------------------
 state (0)  A[0]:(8.50856304169e-06) A[1]:(0.998450219631) A[2]:(4.16934490204e-05)
 state (1)  A[0]:(0.997562587261) A[1]:(1.58846378326e-05) A[2]:(0.997541427612)
 state (2)  A[0]:(1.83135271072e-05) A[1]:(0.99638825655) A[2]:(5.17070293427e-06)
 state (3)  A[0]:(0.996800780296) A[1]:(-2.56896018982e-05) A[2]:(0.996780753136)
--------------------------------------------------
 state (0)  A[0]:(-6.69807195663e-05) A[1]:(0.998506844044) A[2]:(-1.02967023849e-05)
 state (1)  A[0]:(0.997663021088) A[1]:(3.8206577301e-05) A[2]:(0.997645139694)
 state (2)  A[0]:(-4

--------------------------------------------------
 state (0)  A[0]:(4.3511390686e-06) A[1]:(0.99901753664) A[2]:(4.93228435516e-06)
 state (1)  A[0]:(0.998548448086) A[1]:(1.13248825073e-06) A[2]:(0.998549163342)
 state (2)  A[0]:(1.92523002625e-05) A[1]:(0.997874498367) A[2]:(3.92645597458e-05)
 state (3)  A[0]:(0.998056948185) A[1]:(-1.69277191162e-05) A[2]:(0.998060107231)
--------------------------------------------------
 state (0)  A[0]:(6.55651092529e-06) A[1]:(0.99902677536) A[2]:(4.52995300293e-06)
 state (1)  A[0]:(0.998564720154) A[1]:(-1.74939632416e-05) A[2]:(0.998567521572)
 state (2)  A[0]:(3.68356704712e-05) A[1]:(0.997900009155) A[2]:(1.21742486954e-05)
 state (3)  A[0]:(0.998079240322) A[1]:(-1.33514404297e-05) A[2]:(0.998084783554)
--------------------------------------------------
 state (0)  A[0]:(3.22312116623e-05) A[1]:(0.999039649963) A[2]:(8.67694616318e-05)
 state (1)  A[0]:(0.998586237431) A[1]:(6.94394111633e-05) A[2]:(0.998589634895)
 state (2)  A[0]:(-8.0

--------------------------------------------------
 state (0)  A[0]:(-5.46872615814e-06) A[1]:(0.999211966991) A[2]:(1.43647193909e-05)
 state (1)  A[0]:(0.998872816563) A[1]:(5.8114528656e-06) A[2]:(0.998876094818)
 state (2)  A[0]:(1.29342079163e-05) A[1]:(0.998344480991) A[2]:(1.160800457e-05)
 state (3)  A[0]:(0.998477220535) A[1]:(-1.37686729431e-05) A[2]:(0.99848228693)
--------------------------------------------------
 state (0)  A[0]:(0.000877797370777) A[1]:(0.999220311642) A[2]:(0.0023495957721)
 state (1)  A[0]:(0.998887479305) A[1]:(3.84449958801e-06) A[2]:(0.998892366886)
 state (2)  A[0]:(0.00234870170243) A[1]:(0.998358309269) A[2]:(0.0011451090686)
 state (3)  A[0]:(0.99849820137) A[1]:(-0.00125592877157) A[2]:(0.998498797417)
--------------------------------------------------
 state (0)  A[0]:(-1.9833445549e-05) A[1]:(0.999224841595) A[2]:(-1.31875276566e-05)
 state (1)  A[0]:(0.998893260956) A[1]:(3.96370887756e-06) A[2]:(0.998897075653)
 state (2)  A[0]:(1.111626625

--------------------------------------------------
 state (0)  A[0]:(-8.21053981781e-06) A[1]:(0.999320089817) A[2]:(-3.6358833313e-06)
 state (1)  A[0]:(0.99904948473) A[1]:(5.03659248352e-06) A[2]:(0.999054968357)
 state (2)  A[0]:(1.00582838058e-05) A[1]:(0.998597800732) A[2]:(1.40815973282e-05)
 state (3)  A[0]:(0.998709022999) A[1]:(-4.50015068054e-06) A[2]:(0.9987154603)
--------------------------------------------------
 state (0)  A[0]:(-0.000961094803642) A[1]:(0.99932461977) A[2]:(0.000288918614388)
 state (1)  A[0]:(0.999055862427) A[1]:(0.000165194272995) A[2]:(0.999062120914)
 state (2)  A[0]:(0.000557109655347) A[1]:(0.998606443405) A[2]:(0.00030654668808)
 state (3)  A[0]:(0.9987205863) A[1]:(-0.000445693702204) A[2]:(0.998724281788)
--------------------------------------------------
 state (0)  A[0]:(1.64955854416e-05) A[1]:(0.999326765537) A[2]:(-3.53306531906e-05)
 state (1)  A[0]:(0.999061465263) A[1]:(-1.1533498764e-05) A[2]:(0.999066472054)
 state (2)  A[0]:(2.2336

In [ ]:
import matplotlib.pyplot as plt

plt.plot(loss_cum)
#plt.plot([1,2,3,4])
plt.show()


In [25]:
for l in loss_cum:
    print l


tensor(0.4900)
tensor(0.4631)
tensor(0.4278)
tensor(0.4215)
tensor(0.3812)
tensor(0.3449)
tensor(0.3114)
tensor(0.2878)
tensor(0.2670)
tensor(0.2490)
tensor(0.2536)
tensor(0.2465)
tensor(0.2560)
tensor(0.2515)
tensor(0.2506)
tensor(0.2572)
tensor(0.2642)
tensor(0.2575)
tensor(0.2592)
tensor(0.2713)
tensor(0.2538)
tensor(0.2461)
tensor(0.2596)
tensor(0.2357)
tensor(0.2466)
tensor(0.2185)
tensor(0.2376)
tensor(0.2248)
tensor(0.2311)
tensor(0.2362)
tensor(0.2265)
tensor(0.2200)
tensor(0.2307)
tensor(0.2320)
tensor(0.2002)
tensor(0.2235)
tensor(0.2148)
tensor(0.2185)
tensor(0.2194)
tensor(0.2148)
tensor(0.2180)
tensor(0.2110)
tensor(0.2125)
tensor(0.2010)
tensor(0.2083)
tensor(0.1905)
tensor(0.2116)
tensor(0.1992)
tensor(0.2053)
tensor(0.1949)
tensor(0.2061)
tensor(0.2035)
tensor(0.2030)
tensor(0.2208)
tensor(0.2079)
tensor(0.1980)
tensor(0.2075)
tensor(0.2057)
tensor(0.1945)
tensor(0.1968)
tensor(0.1853)
tensor(0.2041)
tensor(0.2073)
tensor(0.2239)
tensor(0.2058)
tensor(0.2157)
tensor(0.2

tensor(0.1705)
tensor(0.1395)
tensor(0.1674)
tensor(0.1712)
tensor(0.1563)
tensor(0.1782)
tensor(0.1749)
tensor(0.1779)
tensor(0.1725)
tensor(0.1741)
tensor(0.1879)
tensor(0.1567)
tensor(0.1864)
tensor(0.1976)
tensor(0.1913)
tensor(0.1755)
tensor(0.1635)
tensor(0.1940)
tensor(0.1890)
tensor(0.1683)
tensor(0.1565)
tensor(0.1643)
tensor(0.1630)
tensor(0.1787)
tensor(0.1765)
tensor(0.1804)
tensor(0.1795)
tensor(0.1417)
tensor(0.1603)
tensor(0.1596)
tensor(0.1624)
tensor(0.1584)
tensor(0.1734)
tensor(0.1697)
tensor(0.1846)
tensor(0.1439)
tensor(0.1484)
tensor(0.1624)
tensor(0.1791)
tensor(0.1679)
tensor(0.1580)
tensor(0.1465)
tensor(0.1768)
tensor(0.1541)
tensor(0.1609)
tensor(0.1996)
tensor(0.1786)
tensor(0.1734)
tensor(0.1746)
tensor(0.1910)
tensor(0.2005)
tensor(0.1795)
tensor(0.1692)
tensor(0.1780)
tensor(0.1922)
tensor(0.1877)
tensor(0.1818)
tensor(0.1588)
tensor(0.1701)
tensor(0.1585)
tensor(0.1615)
tensor(0.1730)
tensor(0.1670)
tensor(0.2015)
tensor(0.1951)
tensor(0.1710)
tensor(0.1

tensor(1.00000e-03 *
       1.7201)
tensor(1.00000e-03 *
       1.6646)
tensor(1.00000e-03 *
       1.8525)
tensor(1.00000e-03 *
       1.7217)
tensor(1.00000e-03 *
       1.8265)
tensor(1.00000e-03 *
       1.5343)
tensor(1.00000e-03 *
       1.6195)
tensor(1.00000e-03 *
       1.7026)
tensor(1.00000e-03 *
       1.5577)
tensor(1.00000e-03 *
       1.7948)
tensor(1.00000e-03 *
       1.7446)
tensor(1.00000e-03 *
       1.4000)
tensor(1.00000e-03 *
       1.7105)
tensor(1.00000e-03 *
       1.5396)
tensor(1.00000e-03 *
       1.6554)
tensor(1.00000e-03 *
       1.6079)
tensor(1.00000e-03 *
       1.3065)
tensor(1.00000e-03 *
       1.6349)
tensor(1.00000e-03 *
       1.2289)
tensor(1.00000e-03 *
       1.7248)
tensor(1.00000e-03 *
       1.3310)
tensor(1.00000e-03 *
       1.4424)
tensor(1.00000e-03 *
       1.6390)
tensor(1.00000e-03 *
       1.4010)
tensor(1.00000e-03 *
       1.3840)
tensor(1.00000e-03 *
       1.4339)
tensor(1.00000e-03 *
       1.2802)
tensor(1.00000e-03 *
       

tensor(1.00000e-04 *
       4.8683)
tensor(1.00000e-04 *
       3.8172)
tensor(1.00000e-04 *
       4.5267)
tensor(1.00000e-04 *
       4.5679)
tensor(1.00000e-04 *
       4.3972)
tensor(1.00000e-04 *
       4.1171)
tensor(1.00000e-04 *
       4.2019)
tensor(1.00000e-04 *
       3.7971)
tensor(1.00000e-04 *
       3.9610)
tensor(1.00000e-04 *
       4.9211)
tensor(1.00000e-04 *
       3.6500)
tensor(1.00000e-04 *
       3.7168)
tensor(1.00000e-04 *
       4.3426)
tensor(1.00000e-04 *
       4.3265)
tensor(1.00000e-04 *
       4.7691)
tensor(1.00000e-04 *
       4.8009)
tensor(1.00000e-04 *
       4.0116)
tensor(1.00000e-04 *
       4.9855)
tensor(1.00000e-04 *
       3.7745)
tensor(1.00000e-04 *
       4.3094)
tensor(1.00000e-04 *
       4.5192)
tensor(1.00000e-04 *
       4.4456)
tensor(1.00000e-04 *
       3.9120)
tensor(1.00000e-04 *
       3.6146)
tensor(1.00000e-04 *
       4.4924)
tensor(1.00000e-04 *
       4.4242)
tensor(1.00000e-04 *
       4.7041)
tensor(1.00000e-04 *
       

tensor(1.00000e-04 *
       2.1273)
tensor(1.00000e-04 *
       2.2170)
tensor(1.00000e-04 *
       2.3734)
tensor(1.00000e-04 *
       2.2599)
tensor(1.00000e-04 *
       1.9488)
tensor(1.00000e-04 *
       2.4569)
tensor(1.00000e-04 *
       2.4793)
tensor(1.00000e-04 *
       1.7498)
tensor(1.00000e-04 *
       1.8438)
tensor(1.00000e-04 *
       2.1097)
tensor(1.00000e-04 *
       1.9607)
tensor(1.00000e-04 *
       2.3994)
tensor(1.00000e-04 *
       4.6036)
tensor(1.00000e-04 *
       2.4528)
tensor(1.00000e-04 *
       3.8383)
tensor(1.00000e-04 *
       4.7752)
tensor(1.00000e-04 *
       2.3829)
tensor(1.00000e-04 *
       5.1872)
tensor(1.00000e-04 *
       5.3598)
tensor(1.00000e-04 *
       2.6492)
tensor(1.00000e-04 *
       7.5240)
tensor(1.00000e-04 *
       3.6954)
tensor(1.00000e-04 *
       3.9779)
tensor(1.00000e-04 *
       4.7952)
tensor(1.00000e-04 *
       3.2265)
tensor(1.00000e-03 *
       1.4983)
tensor(1.00000e-03 *
       2.4105)
tensor(1.00000e-04 *
       

...

tensor(1.00000e-06 *
       3.8322)
tensor(1.00000e-06 *
       3.4897)
tensor(1.00000e-06 *
       3.7290)
tensor(1.00000e-06 *
       3.3722)
tensor(1.00000e-06 *
       3.7703)
tensor(1.00000e-06 *
       3.2166)
tensor(1.00000e-06 *
       3.1362)
tensor(1.00000e-06 *
       4.5570)
tensor(1.00000e-06 *
       4.5713)
tensor(1.00000e-06 *
       4.7499)
tensor(1.00000e-06 *
       4.4069)
tensor(1.00000e-06 *
       4.5797)
tensor(1.00000e-06 *
       3.7930)
tensor(1.00000e-06 *
       4.4477)
tensor(1.00000e-06 *
       3.2470)
tensor(1.00000e-06 *
       3.5015)
tensor(1.00000e-06 *
       4.0933)
tensor(1.00000e-06 *
       3.4210)
tensor(1.00000e-06 *
       4.0794)
tensor(1.00000e-06 *
       4.5213)
tensor(1.00000e-06 *
       4.2779)
tensor(1.00000e-06 *
       3.0503)
tensor(1.00000e-06 *
       3.7901)
tensor(1.00000e-06 *
       3.9324)
tensor(1.00000e-06 *
       3.7674)
tensor(1.00000e-06 *
       3.7814)
tensor(1.00000e-06 *
       4.0643)
tensor(1.00000e-06 *
       

tensor(1.00000e-06 *
       3.2963)
tensor(1.00000e-06 *
       4.0041)
tensor(1.00000e-06 *
       3.4695)
tensor(1.00000e-06 *
       3.0340)
tensor(1.00000e-06 *
       3.4938)
tensor(1.00000e-06 *
       4.1178)
tensor(1.00000e-06 *
       2.8967)
tensor(1.00000e-06 *
       3.1196)
tensor(1.00000e-06 *
       3.6177)
tensor(1.00000e-06 *
       3.5345)
tensor(1.00000e-06 *
       3.1746)
tensor(1.00000e-06 *
       3.5166)
tensor(1.00000e-06 *
       3.5904)
tensor(1.00000e-06 *
       3.3554)
tensor(1.00000e-06 *
       3.5316)
tensor(1.00000e-06 *
       4.4738)
tensor(1.00000e-06 *
       3.0722)
tensor(1.00000e-06 *
       3.7529)
tensor(1.00000e-06 *
       4.2521)
tensor(1.00000e-06 *
       3.7132)
tensor(1.00000e-06 *
       3.5815)
tensor(1.00000e-06 *
       3.3606)
tensor(1.00000e-06 *
       3.4291)
tensor(1.00000e-06 *
       3.8778)
tensor(1.00000e-06 *
       3.5967)
tensor(1.00000e-06 *
       3.4608)
tensor(1.00000e-06 *
       3.5832)
tensor(1.00000e-06 *
       

tensor(1.00000e-06 *
       5.5651)
tensor(1.00000e-06 *
       8.8174)
tensor(1.00000e-06 *
       3.4857)
tensor(1.00000e-06 *
       7.8462)
tensor(1.00000e-06 *
       5.6912)
tensor(1.00000e-06 *
       4.2152)
tensor(1.00000e-06 *
       4.7629)
tensor(1.00000e-06 *
       5.8787)
tensor(1.00000e-06 *
       4.8059)
tensor(1.00000e-06 *
       4.0092)
tensor(1.00000e-06 *
       4.2381)
tensor(1.00000e-06 *
       3.4318)
tensor(1.00000e-06 *
       4.0937)
tensor(1.00000e-06 *
       3.9580)
tensor(1.00000e-06 *
       4.0655)
tensor(1.00000e-06 *
       4.6185)
tensor(1.00000e-06 *
       4.6765)
tensor(1.00000e-06 *
       5.1920)
tensor(1.00000e-06 *
       3.6642)
tensor(1.00000e-06 *
       6.4041)
tensor(1.00000e-06 *
       3.6034)
tensor(1.00000e-06 *
       4.5488)
tensor(1.00000e-06 *
       4.4328)
tensor(1.00000e-06 *
       5.6090)
tensor(1.00000e-06 *
       4.9235)
tensor(1.00000e-06 *
       4.0603)
tensor(1.00000e-06 *
       4.6110)
tensor(1.00000e-06 *
       

tensor(1.00000e-06 *
       3.3506)
tensor(1.00000e-06 *
       3.8109)
tensor(1.00000e-06 *
       2.7108)
tensor(1.00000e-06 *
       3.8197)
tensor(1.00000e-06 *
       3.8428)
tensor(1.00000e-06 *
       3.6776)
tensor(1.00000e-06 *
       3.7628)
tensor(1.00000e-06 *
       3.3689)
tensor(1.00000e-06 *
       3.7270)
tensor(1.00000e-06 *
       3.5336)
tensor(1.00000e-06 *
       3.2884)
tensor(1.00000e-06 *
       3.7742)
tensor(1.00000e-06 *
       3.5788)
tensor(1.00000e-06 *
       4.6016)
tensor(1.00000e-06 *
       3.3177)
tensor(1.00000e-06 *
       2.9440)
tensor(1.00000e-06 *
       3.0540)
tensor(1.00000e-06 *
       3.8662)
tensor(1.00000e-06 *
       3.1451)
tensor(1.00000e-06 *
       4.3663)
tensor(1.00000e-06 *
       3.2467)
tensor(1.00000e-06 *
       4.0438)
tensor(1.00000e-06 *
       3.4722)
tensor(1.00000e-06 *
       3.8341)
tensor(1.00000e-06 *
       4.5654)
tensor(1.00000e-06 *
       4.4001)
tensor(1.00000e-06 *
       3.3082)
tensor(1.00000e-06 *
       

KeyboardInterrupt: 